# Positioning Our Rings

As mentioned before, our bootstrap ring will be around the equator; this is both the easiest place to build it and the most useful for future space launches. Determining this positions of the other rings is more complicated, but boils down to an optimization problem.

## Deciding Factors

There are a number of factors you might consider when deciding on ring positions:

- Population centers within tether range (or within an arbitrary driving range from a potential tether station)
- Major shipping origins and destinations
- Datacenters and industrial facilities requiring substantial power

For the purposes of this chapter, our approach will focus entirely on population, for a number of reasons:

- It's easy to define; lists of all populated areas with their populations and coordinates are readily available
- Given our ability to deliver power at tremendously reduced prices means that datacenters and industrial facilities will almost certainly locate themselves near the rings
- The same is true to a large extent for shipping infrastructure, with the added factor that most major ports and shipping hubs are located in or near populated areas

## Defining A Ring

There are two ways we can define the position of a ring and both have their uses. The first is by defining a great circle between two points, and the second is the normal of its plane.

### Great Circles

Given two points on the surface of the Earth -- say, two cities -- there is one unique circle that passes through the center of the Earth and touches both points. (As long as the points are exactly opposite each other.) This is a great circle, and it's commonly used in aviation because the arc along that great circle is the shortest path between those two points. Because it defines a circle all the way around the Earth, passing through its center, this makes it easy to define a ring by saying "it passes through New York and London."

### Plane Normal

We can imagine a plane cutting the Earth in two equal parts (assuming a spherical Earth), with the center of our ring sitting on that plane. The normal is the direction perpendicular to that plane.

### Conversion From Great Circle To Normal

To convert from the great circle form to the normal form, we can convert the coordinates for our two points into a point in or on the unit sphere, then take the cross product and normalize it. Normalizing the points before taking the cross product isn't necessary for this purpose, but we'll want them in that form for other operations later.

$$Normalize(\vec{x}) = \frac{\vec{x}}{\|{x}\|}$$
$$ToVector(lat, lon) = Normalize(\begin{bmatrix} cos(lat) * cos(lon) & cos(lat) * sin(lon) & sin(lat) \end{bmatrix})$$
$$ToPlaneNormal(\vec{A}, \vec{B}) = Normalize(\vec{A} \times \vec{B})$$

Given two points on earth, we can convert their latitude and longitude to vectors and then calculate the plane normal for that great circle.

### Conversion From Normal To Great Circle

We can't get the original coordinates back from normal form to the great circle form, but this can be useful for some purposes.

XXX: Add this

## Distances

There are two last bits of math we need to know about to figure out how to position our rings: the distance a tether can reach, and the distance from a location on Earth to a ring's normal.

If the Earth was flat, we could just consider the distance a tether could reach as the base of a right triangle, the opposite side length being the altitude of the ring, and the hypotenous our maximum tether length. However, the Earth isn't flat, and over the several hundred kilometers of reach, the curvature of the Earth does actually mean that our tether can't quite reach as far.

Given the Earth's radius as R, ring altitude as D, and tether length as L (all in km), we can find the distance across the Earth's surface -- from a point directly under the ring -- that we can reach with tethers.

$$Reach(R, D, L) = R * acos \frac{R^2 + (R + D)^2 - L^2}{2 * R * (R + D)}$$

XXX: Show derivation. Given a point A=(0, R) and a point B=(0, R+D), define a point C = A rotated by $\theta$. The euclidean distance from B to C is equal to our tether length. Solve for $\theta$, multiply by R to get the arc length along the surface.

Finally, the distance from the ring (or rather, a point on the surface under the ring) to any given point is a matter of finding the angle between the plane and the point, then multiplying by the Earth's radius. Because our normal is perpendicular to the plane, we need to offset that angle by $90^{\circ}$.

Given the Earth's radius as R, ring normal as N, and the point as P:

$$DistanceToNormal(R, \vec{N}, \vec{P}) = R * (\frac{\pi}{2} - acos \left|\hat{N} \cdot \hat{P}\right|)$$

If you look carefully, you'll notice that both Reach and DistanceToNormal are multiplied by the Earth's radius. This is because they both return an angle in radians. In most cases, e.g. checking if a city is within range of a ring with a given max tether length, we can operate directly on that angle instead of thinking about the actual distance along the ground.

## Framing Our Goal

We want to find a ring normal that puts the maximum number of people within range of our tethers. If we were simply trying to find a ring normal that's minimizes the distance to cities, weighted by population, this would be a straightforward regression; we have a threshold under which cities can't be reached, which means this isn't an option.